In [231]:
%reset
import os
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns


# activate Bokeh output in Jupyter notebook
from bokeh.io import output_notebook

output_notebook()


sns.set(font_scale=2,style='whitegrid') 
pd.set_option('max_colwidth',100)

Once deleted, variables cannot be recovered. Proceed (y/[n])? y


Loading BokehJS ...

In [232]:
datapath = 'python_approach_qc/'
files = os.listdir(datapath)
files_pos = [f for f in files if f.endswith('posvars_approach.csv')]
files_lfp = [f for f in files if f.endswith('lfpvars_approach.csv')]

In [233]:
files_pos

['LH16_D25_posvars_approach.csv',
 'LH08_D32_posvars_approach.csv',
 'LH02_D11_posvars_approach.csv',
 'LH02_D14_posvars_approach.csv',
 'LH09_D04_posvars_approach.csv',
 'LH09_D08_posvars_approach.csv',
 'LH16_D09_posvars_approach.csv',
 'LH16_D42_posvars_approach.csv',
 'LH16_D11_posvars_approach.csv',
 'LH16_D29_posvars_approach.csv',
 'LH09_D15_posvars_approach.csv',
 'LH16_D23_posvars_approach.csv',
 'LH16_D43_posvars_approach.csv',
 'LH08_D28_posvars_approach.csv',
 'LH03_D18_posvars_approach.csv',
 'LH03_D20_posvars_approach.csv',
 'LH09_D09_posvars_approach.csv',
 'LH16_D22_posvars_approach.csv',
 'LH16_D10_posvars_approach.csv']

In [234]:
files_lfp

['LH03_D18_TETFP11_lfpvars_approach.csv',
 'LH02_D11_TETFP06_lfpvars_approach.csv',
 'LH16_D10_TETFP33_lfpvars_approach.csv',
 'LH09_D08_TETFP13_lfpvars_approach.csv',
 'LH16_D42_TETFP37_lfpvars_approach.csv',
 'LH16_D29_TETFP37_lfpvars_approach.csv',
 'LH16_D42_TETFP33_lfpvars_approach.csv',
 'LH16_D09_TETFP29_lfpvars_approach.csv',
 'LH16_D22_TETFP25_lfpvars_approach.csv',
 'LH16_D43_TETFP49_lfpvars_approach.csv',
 'LH16_D23_TETFP29_lfpvars_approach.csv',
 'LH16_D29_TETFP33_lfpvars_approach.csv',
 'LH03_D20_TETFP61_lfpvars_approach.csv',
 'LH08_D32_TETFP09_lfpvars_approach.csv',
 'LH03_D18_TETFP49_lfpvars_approach.csv',
 'LH16_D23_TETFP09_lfpvars_approach.csv',
 'LH09_D15_TETFP13_lfpvars_approach.csv',
 'LH03_D18_TETFP87_lfpvars_approach.csv',
 'LH08_D32_TETFP53_lfpvars_approach.csv',
 'LH16_D23_TETFP53_lfpvars_approach.csv',
 'LH09_D09_TETFP53_lfpvars_approach.csv',
 'LH08_D28_TETFP29_lfpvars_approach.csv',
 'LH16_D11_TETFP37_lfpvars_approach.csv',
 'LH02_D14_TETFP16_lfpvars_approac

In [235]:
#iterate over the lfp files, and within the loop
#grab the relevant position file
file = 0
lfpfile = pd.read_csv(os.path.join(datapath,files_lfp[file]))

trial = 1 
odorblock = 1
subtrial = lfpfile[(lfpfile['trial_labels_lfplen']==trial) & (lfpfile['odor_block_labels_lfplen']==odorblock)]

lfp = subtrial['lfp_approach'].values
lfptime = subtrial['time'].values

#find the corresponding position file
posfilename = files_lfp[file].split('TET')[0] + 'posvars_approach.csv'
posfile = pd.read_csv(os.path.join(datapath,posfilename))

subtrialpos = posfile[(posfile['trial_labels_poslen']==trial) & (posfile['odor_block_labels_poslen']==odorblock)]
vsm = subtrialpos['vsm'].values
postime = subtrialpos['vposts'].values

In [220]:
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, BoxZoomTool, PanTool, CustomJS
from bokeh.layouts import gridplot

source1 = ColumnDataSource(data=dict(x=lfptime, y=lfp))
source2 = ColumnDataSource(data=dict(x=postime, y=vsm))

# Create the first subplot
p1 = figure(plot_width=900, plot_height=200, tools="box_zoom,box_select,pan,reset,tap,zoom_out")
p1.line(x='x', y='y', source=source1)

# Create the second subplot
p2 = figure(plot_width=900, plot_height=200, tools="box_zoom,box_select,pan,reset,tap,zoom_out")
p2.line(x='x', y='y', source=source2)

# Link the x range between the two subplots
p1.x_range = p2.x_range

# Create a grid layout to display both subplots
layout = gridplot([[p1], [p2]])

show(layout)

In [177]:
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, BoxZoomTool, PanTool, CustomJS
from bokeh.layouts import gridplot

source1 = ColumnDataSource(data=dict(x=lfptime, y=lfp))
source2 = ColumnDataSource(data=dict(x=postime, y=vsm))

# Create the first subplot
p1 = figure(plot_width=900, plot_height=200, tools="box_zoom,box_select,pan,tap,reset")
p1.line(x='x', y='y', source=source1)

# Create the second subplot
p2 = figure(plot_width=900, plot_height=200, tools="box_zoom,box_select,pan,tap,reset")
p2.line(x='x', y='y', source=source2)

# Link the x range between the two subplots
p1.x_range = p2.x_range

# Create a callback to capture selected range
callback = CustomJS(args=dict(source=source1), code="""
    // Get the selected range from the box_select tool
    const data = source.data;
    const x = data['x'];
    const selected = cb_obj.geometry['x'];
    
    // Extract the selected x values
    const startIdx = Math.min(selected[0], selected[2]);
    const endIdx = Math.max(selected[0], selected[2]);
    const selectedXValues = x.slice(startIdx, endIdx + 1);
    
    // Print the selected x values (you can process or use them as needed)
    console.log("Selected X Values: ", selectedXValues);
""")

# Add the box select callback to both subplots
p1.js_on_change('box_select',callback)
p2.js_on_change('box_select',callback)


# Create a grid layout to display both subplots
layout = gridplot([[p1], [p2]])

show(layout)




In [178]:
print(source1.selected)

Selection(id='45596', ...)


In [146]:
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, BoxZoomTool, PanTool, CustomJS
from bokeh.layouts import gridplot

source1 = ColumnDataSource(data=dict(x=lfptime, y=lfp))
source2 = ColumnDataSource(data=dict(x=postime, y=vsm))

# Create the first subplot
p1 = figure(plot_width=900, plot_height=200, tools="box_zoom,box_select,pan,tap,reset")
p1.line(x='x', y='y', source=source1)

# Create the second subplot
p2 = figure(plot_width=900, plot_height=200, tools="box_zoom,box_select,pan,tap,reset")
p2.line(x='x', y='y', source=source2)

# Link the x range between the two subplots
p1.x_range = p2.x_range

# Create a callback to capture selected range
selected_x_values = []

callback = CustomJS(args=dict(source=source1, selected_x_values=selected_x_values), code="""
    const selected = source.selected['1d'].indices;
    selected_x_values.push(selected);
    console.log("Selected X Values: ", selected_x_values);
""")

# Add the custom JavaScript callback to both subplots
p1.js_on_event('box_select', callback)
p2.js_on_event('box_select', callback)

# Create a grid layout to display both subplots
layout = gridplot([[p1], [p2]])

show(layout)



In [184]:
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, BoxZoomTool, CustomJS
from bokeh.layouts import gridplot

output_notebook()


source1 = ColumnDataSource(data=dict(x=lfptime, y=lfp))
source2 = ColumnDataSource(data=dict(x=postime, y=vsm))


# Create the first subplot
p1 = figure(plot_width=900, plot_height=200, tools="box_zoom,box_select,pan,zoom_out,reset")
p1.line(x='x', y='y', source=source1)

# Create the second subplot
p2 = figure(plot_width=900, plot_height=200, tools="box_zoom,box_select,pan,zoom_out,reset")
p2.line(x='x', y='y', source=source2)

# Link the x range between the two subplots
p1.x_range = p2.x_range


callback = CustomJS(args=dict(source=source1), code="""
                     console.log('Running CustomJS callback now.');
                     var indices = source.selected.indices;
                     var kernel = IPython.notebook.kernel;
                     kernel.execute("selected_indices = " + indices)
                     """)

# Add the custom JavaScript callback to both subplots
# it should run when a selection event occurs in the figure
p1.js_on_event('box_selection', callback)
p2.js_on_event('box_selection', callback)

# Create a grid layout to display both subplots
layout = gridplot([[p1], [p2]])

show(layout)

# inspect the selected indices
selected_indices

# use the indices to create lists of the selected values
lfp_selected, vsm_selected = [], []
for indice in selected_indices:
    lfp_val = source1.data['x'][indice]
    lfp_selected.append(lfp_val)
    vsm_val = source2.data['x'][indice]
    vsm_selected.append(vsm_val)
    
# make a column data souce containing the selected values
selected = ColumnDataSource(data=dict(x=lfp_selected, y=vsm_selected))

# inspect the selected data
selected.data


Loading BokehJS ...

{'x': [], 'y': []}

In [236]:
from random import random
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
from bokeh.models.sources import ColumnDataSource
from bokeh.models.callbacks import CustomJS

output_notebook()


s = ColumnDataSource(data=dict(x=lfptime, y=lfp))


fig = figure(plot_width=900, plot_height=200,tools=['box_select', 'lasso_select', 'box_zoom', 'reset'])
fig.scatter("x", "y", source=s, alpha=0.6)

# make a custom javascript callback that exports the indices of the selected points to the Jupyter notebook
callback = CustomJS(args=dict(s=s), 
                    code="""
                         console.log('Running CustomJS callback now.');
                         var indices = s.selected.indices;
                         var kernel = IPython.notebook.kernel;
                         kernel.execute("selected_indices = " + indices)
                         """)

# set the callback to run when a selection geometry event occurs in the figure
fig.js_on_event('selectiongeometry', callback)

show(fig)

# make a selection using a selection tool 




Loading BokehJS ...

In [237]:
# inspect the selected indices
selected_indices

# use the indices to create lists of the selected values
x_selected, y_selected = [], []
for indice in selected_indices:
    x_val = s.data['x'][indice]
    y_val = s.data['y'][indice]
    x_selected.append(x_val)
    y_selected.append(y_val)
    
# make a column data souce containing the selected values
selected = ColumnDataSource(data=dict(x=x_selected, y=y_selected))

# inspect the selected data
selected.data

{'x': [506.705525,
  506.706525,
  506.707525,
  506.708525,
  506.709525,
  506.710525,
  506.711525,
  506.712525,
  506.713525,
  506.714525,
  506.715525,
  506.716525,
  506.717525,
  506.718525,
  506.719525,
  506.720525,
  506.721525,
  506.722525,
  506.723525,
  506.724525,
  506.725525,
  506.726525,
  506.727525,
  506.728525,
  506.729525,
  506.730525,
  506.731525,
  506.732525,
  506.733525,
  506.734525,
  506.735525,
  506.736525,
  506.737525,
  506.738525,
  506.739525,
  506.740525,
  506.741525,
  506.742525,
  506.743525,
  506.744525,
  506.745525,
  506.746525,
  506.747525,
  506.748525,
  506.749525,
  506.750525,
  506.751525,
  506.752525,
  506.753525,
  506.754525,
  506.755525,
  506.756525,
  506.757525,
  506.758525,
  506.759525,
  506.760525,
  506.761525,
  506.762525,
  506.763525,
  506.764525,
  506.765525,
  506.766525,
  506.767525,
  506.768525,
  506.769525,
  506.770525,
  506.771525,
  506.772525,
  506.773525,
  506.774525,
  506.775525,
 

In [242]:
selected.data['x'][0],selected.data['x'][-1]

(506.705525, 509.545525)

In [262]:
from random import random
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
from bokeh.models.sources import ColumnDataSource
from bokeh.models.callbacks import CustomJS

output_notebook()


s = ColumnDataSource(data=dict(x=lfptime, y=lfp))


fig = figure(plot_width=900, plot_height=200,tools=['box_select', 'pan', 'lasso_select', 'box_zoom', 'reset'])
fig.line("x", "y", source=s, alpha=0.6)
fig.circle("x", "y", source=s, fill_color='white', size=4)


# make a custom javascript callback that exports the indices of the selected points to the Jupyter notebook
callback = CustomJS(args=dict(s=s), 
                    code="""
                         console.log('Running CustomJS callback now.');
                         var indices = s.selected.indices;
                         var kernel = IPython.notebook.kernel;
                         kernel.execute("selected_indices = " + indices)
                         """)

# set the callback to run when a selection geometry event occurs in the figure
fig.js_on_event('selectiongeometry', callback)

show(fig)

# make a selection using a selection tool 


Loading BokehJS ...

In [263]:
# inspect the selected indices
selected_indices

# use the indices to create lists of the selected values
x_selected, y_selected = [], []
for indice in selected_indices:
    x_val = s.data['x'][indice]
    y_val = s.data['y'][indice]
    x_selected.append(x_val)
    y_selected.append(y_val)
    
# make a column data souce containing the selected values
selected = ColumnDataSource(data=dict(x=x_selected, y=y_selected))

# inspect the selected data
selected.data

{'x': [508.111525,
  508.112525,
  508.113525,
  508.114525,
  508.115525,
  508.116525,
  508.117525,
  508.118525,
  508.119525,
  508.120525,
  508.121525,
  508.122525,
  508.123525,
  508.124525,
  508.125525,
  508.126525,
  508.127525,
  508.128525,
  508.129525,
  508.130525,
  508.131525,
  508.132525,
  508.133525,
  508.134525,
  508.135525,
  508.136525,
  508.137525,
  508.138525,
  508.139525,
  508.140525,
  508.141525,
  508.142525,
  508.143525,
  508.144525,
  508.145525,
  508.146525,
  508.147525,
  508.148525,
  508.149525,
  508.150525,
  508.151525,
  508.152525,
  508.153525,
  508.154525,
  508.155525,
  508.156525,
  508.157525,
  508.158525,
  508.159525,
  508.160525,
  508.161525,
  508.162525,
  508.163525,
  508.164525,
  508.165525,
  508.166525,
  508.167525,
  508.168525,
  508.169525,
  508.170525,
  508.171525,
  508.172525,
  508.173525,
  508.174525,
  508.175525,
  508.176525,
  508.177525,
  508.178525,
  508.179525,
  508.180525,
  508.181525,
 

In [264]:
selected.data['x'][0],selected.data['x'][-1]

(508.111525, 509.463525)

In [265]:
509.463525-508.111525

1.3520000000000323